In [1]:
import logging

# Set logging levels to avoid matplotlib warnings
logging.getLogger('matplotlib').setLevel(logging.ERROR)
logging.getLogger('matplotlib.font_manager').setLevel(logging.ERROR)

In [2]:
from prolint2 import Universe
from prolint2.sampledata import GIRKDataSample

GIRK = GIRKDataSample()

pl_u = Universe(GIRK.coordinates, GIRK.trajectory)

/Users/danielramirez/miniforge3/envs/prolint2_test_ws/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
print(f"Trajectory data for GIRK starting at {pl_u.trajectory[0].time/1000000:.0f} us and ending at {pl_u.trajectory[-1].time/1000000:.0f} us, sampled every {pl_u.trajectory.dt/1000:.0f} ns.")

Trajectory data for GIRK starting at 35 us and ending at 40 us, sampled every 4 ns.


In [4]:
pl_u.query, pl_u.database

(<ProLint Wrapper for <AtomGroup with 2956 atoms>>,
 <ProLint Wrapper for <AtomGroup with 20864 atoms>>)

In [5]:
print(f"Membrane lipid composition is {dict(pl_u.database.resname_counts)}.")

Membrane lipid composition is {'POPE': 652, 'POPS': 652, 'CHOL': 652}.


In [6]:
print(f"First five residues of the protein are: {pl_u.query.get_resnames([1, 2, 3, 4, 5], out=dict)}")

First five residues of the protein are: {1: 'ARG', 2: 'GLN', 3: 'ARG', 4: 'TYR', 5: 'MET'}


In [7]:
pl_u.database = pl_u.database.add("LIPX")

In [8]:
pl_u.query = pl_u.query.remove("ARG")
print(f"Number of arginine residues: {pl_u.query.resname_counts['ARG']}")

Number of arginine residues: 0


In [9]:
pl_u.query = pl_u.query.add("ARG")
print(f"Number of arginine residues: {pl_u.query.resname_counts['ARG']}")

Number of arginine residues: 64


In [10]:
pl_u.params

{'units': 'us',
 'normalizer': 'time_fraction',
 'unit_conversion_factor': 1e-06,
 'norm_factor': 0.0008}

In [11]:
pl_u.units = "ns"
pl_u.params

{'units': 'ns',
 'normalizer': 'time_fraction',
 'unit_conversion_factor': 0.001,
 'norm_factor': 0.0008}

In [12]:
pl_u.normalize_by = "actual_time"
pl_u.params

{'units': 'ns',
 'normalizer': 'actual_time',
 'unit_conversion_factor': 0.001,
 'norm_factor': 4.0}

In [13]:
pl_c = pl_u.compute_contacts(cutoff=7.0)

100%|██████████| 1251/1251 [00:09<00:00, 132.56it/s]


In [ ]:
pl_c.contacts[14]

In [ ]:
pl_c.contact_frames[14]

In [16]:
from prolint2.metrics.metrics import Metric, MeanMetric, SumMetric, MaxMetric

metric_instances_list = [MeanMetric(), SumMetric(), MaxMetric()]
metric_instance = Metric(pl_c, metric_instances_list) 
contacts_out = metric_instance.compute() 

In [ ]:
from prolint2.plotting.multiples import MultiplePointDistribution

MPD = MultiplePointDistribution(pl_u, contacts_out)
MPD.create_plot()

In [ ]:
from prolint2.plotting import DensityMap

Dens = DensityMap(pl_u, fig_size=(6, 6))
Dens.create_plot(lipid_type='POPS', interpolation='nearest', cmap='viridis')

In [ ]:
from prolint2.plotting import LogoResidues

LR = LogoResidues(pl_u, contacts_out)
LR.create_plot(lipid_type='POPS', metric_name='MeanMetric')

In [21]:
from prolint2.plotting.utils import get_lipid_contact_durations

get_lipid_contact_durations(pl_u, pl_c, 'POPS', residue_id=461)

Lipip ID  Frequency
0      2622     1244.0
1      2840        1.0

In [ ]:
from prolint2.plotting import InteractionHeatMap

IHM = InteractionHeatMap(pl_u, pl_c)
IHM.create_plot(residue_id=461, lipid_id=2622, palette='Reds')

In [ ]:
from prolint2.plotting import TwoPointDistanceEvolution

TPD = TwoPointDistanceEvolution(pl_u)
TPD.create_plot(lipid_id = 2622, lipid_atomname='PO4', residue_id = 461, residue_atomname='SC2', unit = 'frame', smooth_line = True, n_points = 250, useOffset = True)